# How to develop a MEC application using the MEC Sandbox HTTP REST API

## Table of contents

 .[ What is a MEC applicationn](what_is_a_mec_applicationn)2
.[ The basics of developing a MEC applicationh](the_basics_of_developing_a_mec_application)
3. [Use the MEC Sandbox HTTP REST API models and code](#use_the_mec_sandbox_http_rest_api_models_and_code)
4. [Create our first MEC application](#create_our_first_mec_application)
    4.1. [The login function](#the_login_function)
    4.2. [The logout function](#the_logout_function)
5. [Second step: Retrieve the list of network scenarios](#second_step_retrieve_the_list_of_network_scenarios)
6. [Third step: Activate and deactivate a network scenario](#third_step_activate_and_deactivate_a_network_scenario)
    6.1. [The activate function](#the_activate_function)
    6.2. [The deactivate function](#thedeactivate_function)
7. [Fourth step: Create and delete an appliction instance id](#fourth_step_create_and_delete_an_appliction_instance_id)
8. [MEC Registration and the READY indication](#mec_registration_and_the_ready_indication)
9. [Annexes](#annexes)
10. [Bibliography](#bibliograhypt


## What is a MEC application

See [The Wiki MEC web site](https://www.etsi.org/technologies/multi-access-edge-computing)


## The basics of developing a MEC application

The developement of a MEC application follows a strict process in order to access the ETSI MEC services and provides valueable services to the customers.
Mainly, this process can be split in several steps:
1. Global initializations (constant, variables...)
2. Create of a new instance of a MEC Sandbox (Note that using an existing one could be a solution too (see Annex A)
3. Activate a network scenario in order to access the ETSI MEC services
4. Create a new application identifier
5. Register our MEC application and subscribe to service termination (see MEC 011)
6. Use MEC services in order to provide valueable services to the customers
    6.1. Apply MEC services required subscriptions (e.g. MEC 013 location subscription)
7. Terminate the MEC application
    7.1. Remove MEC services subscriptions
    7.2. Deactivate the current network scenario
    7.3. Delete the instance of the MEC Sandbox
8. Release all the MEC application resources

## Use the MEC Sandbox HTTP REST API models and code

The MEC sandbox provides a piece of code (the python sub) that shall be used to develop the MEC applicationand interact with the MEC Sandbox. This piece of code mainly contains swagger models to serialize/deserialize JSON data structures and HTTP REST API call functions.
The openApi file is availabe [here](https://forge.etsi.org/rep/mec/AdvantEDGE/-/blob/Task2_PoC/go-apps/meep-sandbox-api/api/swagger.yaml) and the [Swagger editor](https://editor-next.swagger.io/) is used to generate the python sub.

The project architecture is describe [here](images/project_arch.jpg).

The api folder contains the python implementation of the HTTP REST API definitions introduced by the openApi [file](https://forge.etsi.org/rep/mec/AdvantEDGE/-/blob/Task2_PoC/go-apps/meep-sandbox-api/api/swagger.yaml).
The model folder contains the python implementation of the data type definitions introduced by the openApi [file](https://forge.etsi.org/rep/mec/AdvantEDGE/-/blob/Task2_PoC/go-apps/meep-sandbox-api/api/swagger.yaml).
irectory:

Before to create our MEC ap[plication skeleton, the following steps shall be done:
1) Change the working directory (see the project architecture)

In [1]:
import os
os.chdir(os.path.join(os.getcwd(), '../mecapp'))
print(os.getcwd())

/home/yann/dev/jupyter/Sandbox/mecapp


2) Do the python import

In [2]:
from __future__ import division # Import floating-point division (1/4=0.25) instead of Euclidian division (1/4=0)

import os
import sys
import logging
import time
import json
import uuid

from pprint import pprint

import swagger_client
from swagger_client.rest import ApiException

from http import HTTPStatus
from http.server import BaseHTTPRequestHandler, HTTPServer


3) to initialize the global constants (cell 3)

In [3]:
MEC_SANDBOX_URL     = 'https://mec-platform.etsi.org'                        # MEC Sandbox host/base URL
MEC_SANDBOX_API_URL = 'https://mec-platform.etsi.org/sandbox-api/v1'         # MEC Sandbox API host/base URL
PROVIDER            = 'Jupyter2024'                                         # Login provider value
MEC_PLTF            = 'mep1'                                                 # MEC plateform name. Linked to the network scenario
LOGGER_FORMAT       = '%(asctime)s - %(name)s - %(levelname)s - %(message)s' # Logging format
STABLE_TIME_OUT     = 6                                                      # Timer to wait for MEC Sndbox reaches its stable state (K8S pods in running state)
LOGIN_TIMEOUT       = 3 #30                                                     # Timer to wait for user to authorize from GITHUB
LISTENER_IP         = '0.0.0.0'                                              # Listener IPv4 address for notification callback calls
LISTENER_PORT       = 32100                                                  # Listener IPv4 port for notification callback calls
CALLBACK_URI        = "/jupyter/sandbox/demo6/v1/"

4) to setup a logger instance and initialize the global variables  (cell 4)

In [4]:
# Initialize the logger
logger = logging.getLogger(__name__)
logger.setLevel(logging.DEBUG)
logging.basicConfig(filename='/tmp/' + time.strftime("%Y%m%d-%H%M%S") + '.log')
l = logging.StreamHandler()
l.setFormatter(logging.Formatter('%(asctime)s - %(name)s - %(levelname)s - %(message)s'))
logger.addHandler(l)

# Setup the HTTP REST API configuration
configuration               = swagger_client.Configuration()
configuration.host          = MEC_SANDBOX_API_URL
configuration.verify_ssl    = False
configuration.debug         = True
configuration.logger_format = LOGGER_FORMAT

# Create an instance of ApiClient to be used before each request
api = swagger_client.ApiClient(configuration, 'Content-Type', 'application/json')

# Initialize the global variables
nw_scenarios    = []   # The list of available network scenarios
nw_scenario_idx = -1   # The network scenario idx to activate (deactivate)
app_inst_id     = None # The requested application instance identifier


## Create our first MEC application

The first step to develop a MEC application is to create the application skeleton which contains the minimum steps below:
 
- Login to instanciate a MEC Sandbox
- Logout to delete a existing MEC Sandbox

### First steps: the login/logout

Here is the first squeleton with the following sequence:
- Login
- Print sandbox identifier
- Logout
- Check that logout is effective


#### The login function

To log to the MEC Sandbox, 
The login process is done in two step. In step 1, a user code is requested to GITHUB. In step 2, the user has to enter this user code to https://github.com/login/device and proceed to the authorization.
Please, pay attention to the log '=======================> DO AUTHORIZATION WITH CODE :' which indicate you the user code to use for the authorization.

It uses the HTTP POST request with the URL 'POST /sandbox-api/v1/login?provide=github' (see PROVIDER constant).


In [5]:
# Login
def process_login() -> str:
    """
    Authenticate and create a new MEC Sandbox instance.

    :return: The sandbox instance identifier on success, None otherwise
    """ 

    global PROVIDER, MEC_SANDBOX_API_URL, logger, configuration

    logger.debug(">>> process_login")

    try:
        auth = swagger_client.AuthorizationApi(api)
        oauth = auth.login(PROVIDER, async_req = False)
        logger.debug("process_login (step1): oauth: " + str(oauth))
        # Wait for the MEC Sandbox is running
        logger.debug("=======================> DO AUTHORIZATION WITH CODE : " + oauth.user_code)
        time.sleep(LOGIN_TIMEOUT) # Wait for Authirization from user side
        namespace = auth.get_namespace(oauth.user_code)
        logger.debug("process_login (step2): result: " + str(namespace))
        return namespace.sandbox_name
    except ApiException as e:
        logger.error("Exception when calling AuthorizationApi->login: %s\n" % e)

    return None
    # End of function process_login


#### The logout function

It uses the HTTP POST request with the URL 'POST /sandbox-api/v1/logout?sandbox_name={sandbox_name}'.


In [6]:
# Logout
def process_logout(sandbox: str) -> int:
    """
    Delete the specified MEC Sandbox instance.

    :param sandbox: The MEC Sandbox to delete
    :return: 0 on success, -1 otherwise
    """

    global PROVIDER, MEC_SANDBOX_API_URL, logger, configuration

    logger.debug(">>> process_logout: sandbox=" + sandbox)

    try:
        auth = swagger_client.AuthorizationApi(api)
        result = auth.logout(sandbox, async_req = False)  # noqa: E501
        return 0
    except ApiException as e:
        logger.error("Exception when calling AuthorizationApi->logout: %s\n" % e)
    return -1
    # End of function process_logout


Now, let put in action our Login/Logout functions:

In [ ]:
def process_main():
    """
    This is the skeleton of our MEC application:
        - Login
        - Print sandbox identifier
        - Logout
        - Check that logout is effective
    This skeleton will be the bas of the next sprint in order to achieve a full implementation of a MEC application
    """ 

    global PROVIDER, MEC_SANDBOX_API_URL, logger

    logger.debug("Starting at " + time.strftime("%Y%m%d-%H%M%S"))
    logger.debug("\t pwd= " + os.getcwd())

    # Login
    sandbox = process_login()
    if sandbox is None:
        return

    # Print sandbox identifier
    logger.info("Sandbox created: " + sandbox)
    # Wait for the MEC Sandbox is running
    time.sleep(STABLE_TIME_OUT) # Wait for k8s pods up and running

    # Logout
    process_logout(sandbox)

    # Check that logout is effective
    logger.debug("To check that logout is effective, verify on the MEC Sandbox server that the MEC Sandbox is removed (kubectl get pods -A")
  
    logger.debug("Stopped at " + time.strftime("%Y%m%d-%H%M%S"))
    # End of function process_main

if __name__ == '__main__':
    process_main()


### Second step: Retrieve the list of network scenarios

Let's go futhur and see how we can retrieve the list of the network scenarios available in order to activate one of them and access the MEC services exposed such as MEC 013 or MEC 030.

The sequence will be:
- Login
- Print sandbox identifier
- Print available network scenarios
- Logout
- Check that logout is effective

The login and logout functions are described in cell 3 and 4.

To retrieve the list of the network scenarios, let's create a new function called 'get_network_scenarios'. It uses the HTTP GET request with the URL '/sandbox-api/v1/sandboxNetworkScenarios?sandbox_name={sandbox_name}'.

In [7]:
def get_network_scenarios(sandbox: str) -> list:
    """
    Retrieve the list of the available network scenarios.

    :param sandbox: The MEC Sandbox instance to use
    :return: The list of the available network scenarios on success, None otherwise
    """

    global PROVIDER, MEC_SANDBOX_API_URL, logger, configuration

    logger.debug(">>> get_network_scenarios: sandbox=" + sandbox)

    try:
        nw = swagger_client.SandboxNetworkScenariosApi(api)
        result = nw.sandbox_network_scenarios_get(sandbox, async_req = False)  # noqa: E501
        logger.debug("get_network_scenarios: result: " + str(result))
        return result
    except ApiException as e:
        logger.error("Exception when calling SandboxNetworkScenariosApi->sandbox_network_scenarios_get: %s\n" % e)

    return None
    # End of function get_network_scenarios


Putting everything together:

In [ ]:
def process_main():
    """
    This is the first sprint of our skeleton of our MEC application:
        - Login
        - Print sandbox identifier
        - Print available network scenarios
        - Logout
        - Check that logout is effective
    """ 
    global PROVIDER, MEC_SANDBOX_API_URL, logger, nw_scenarios 

    logger.debug("Starting at " + time.strftime("%Y%m%d-%H%M%S"))
    logger.debug("\t pwd= " + os.getcwd())

    # Login
    sandbox = process_login()
    if sandbox is None:
        logger.error("Failed to instanciate a MEC Sandbox")
        return

    # Print sandbox identifier
    logger.info("Sandbox created: " + sandbox)
    # Wait for the MEC Sandbox is running
    time.sleep(STABLE_TIME_OUT) # Wait for k8s pods up and running

    # Print available network scenarios
    nw_scenarios = get_network_scenarios(sandbox)
    if nw_scenarios is None:
        logger.error("Failed to retrieve the list of network scenarios")
    elif len(nw_scenarios) != 0:
        logger.info("nw_scenarios: %s", str(type(nw_scenarios[0])))
        logger.info("nw_scenarios: %s", str(nw_scenarios))
    else:
        logger.info("nw_scenarios: No scenario available")

    # Logout
    process_logout(sandbox)

    # Check that logout is effective
    logger.debug("To check that logout is effective, verify on the MEC Sandbox server that the MEC Sandbox is removed (kubectl get pods -A")
  
    logger.debug("Stopped at " + time.strftime("%Y%m%d-%H%M%S"))
    # End of function process_main

if __name__ == '__main__':
    process_main()


### Third step: Activate and deactivate a network scenario

Having a list of network scenarion, the next step is to actvate (and deactivate) a network scenario. This step is mandatory to create a new application instance id and access the MEC services.

In this section, we will arbitrary activate the network scenario called '4g-5g-macro-v2x', which is at the index 0 of the nw_scenarios. 

In [8]:
def select_network_scenario_based_on_criteria(criterias_list: list) -> int:
    """
    Select the network scenario to activate based of the provided list of criterias.

    :param criterias_list: The list of criterias to select the correct network scenario
    :return: 0 on success, -1 otherwise
    """
    return 0 # The index of the '4g-5g-macro-v2x' network scenario - Hard coded

#### The activate function

The process to activate a scenario is based on an HTTP POST request with the URL '/sandboxNetworkScenarios/{sandbox_name}?network_scenario_id={network_scenario_id}'.


In [9]:
def activate_network_scenario(sandbox: str) -> int:
    """
    Activate the specified network scenario.

    :param sandbox: The MEC Sandbox instance to use
    :return: 0 on success, -1 otherwise
    """

    global MEC_SANDBOX_API_URL, logger, configuration, nw_scenarios, nw_scenario_idx

    logger.debug(">>> activate_network_scenario: " + sandbox)

    nw_scenario_idx = select_network_scenario_based_on_criteria([])
    if nw_scenario_idx == -1:
        logger.error("activate_network_scenario: Failed to select a network scenarion")
        return -1

    try:
        nw = swagger_client.SandboxNetworkScenariosApi(api)
        result = nw.sandbox_network_scenario_post(sandbox, nw_scenarios[nw_scenario_idx].id, async_req = False)  # noqa: E501
        logger.debug("activate_network_scenario: result: " + str(result))
        return result
    except ApiException as e:
        logger.error("Exception when calling SandboxNetworkScenariosApi->activate_network_scenario: %s\n" % e)

    return -1
    # End of function activate_network_scenario


#### The deactivate function

The process to deactivate a scenario is based on an HTTP DELETE request with the URL '/sandboxNetworkScenarios/{sandbox_name}?network_scenario_id={network_scenario_id}'.


In [10]:
def deactivate_network_scenario(sandbox: str) -> int:
    """
    Deactivate the current network scenario.

    :param sandbox: The MEC Sandbox instance to use
    :return: 0 on success, -1 otherwise
    """

    global MEC_SANDBOX_API_URL, logger, configuration, nw_scenarios, nw_scenario_idx

    logger.debug(">>> deactivate_network_scenario: " + sandbox)

    try:
        nw = swagger_client.SandboxNetworkScenariosApi(api)
        result = nw.sandbox_network_scenario_delete(sandbox, nw_scenarios[nw_scenario_idx].id, async_req = False)  # noqa: E501
        logger.debug("deactivate_network_scenario: result: " + str(result))
        return result
    except ApiException as e:
        logger.error("Exception when calling SandboxNetworkScenariosApi->deactivate_network_scenario: %s\n" % e)

    return -1
    # End of function deactivate_network_scenario


Now, it is time to create the second iteration of our MEC application.

The sequence is the following:
- Login
- Print sandbox identifier
- Print available network scenarios
- Activate a network scenario
- Check that the network scenario is activated and the MEC services are running
- Deactivate a network scenario
- Logout
- Check that logout is effective



In [ ]:
def process_main():
    """
    This is the second sprint of our skeleton of our MEC application:
        - Login
        - Print sandbox identifier
        - Print available network scenarios
        - Activate a network scenario
        - Check that the network scenario is activated and the MEC services are running
        - Deactivate a network scenario
        - Logout
        - Check that logout is effective
    """ 
    global PROVIDER, MEC_SANDBOX_API_URL, logger, nw_scenarios 

    logger.debug("Starting at " + time.strftime("%Y%m%d-%H%M%S"))
    logger.debug("\t pwd= " + os.getcwd())

    # Login
    sandbox = process_login()
    if sandbox is None:
        logger.error("Failed to instanciate a MEC Sandbox")
        return

    # Print sandbox identifier
    logger.info("Sandbox created: " + sandbox)
    # Wait for the MEC Sandbox is running
    time.sleep(STABLE_TIME_OUT) # Wait for k8s pods up and running

    # Print available network scenarios
    nw_scenarios = get_network_scenarios(sandbox)
    if nw_scenarios is None:
        logger.error("Failed to retrieve the list of network scenarios")
    elif len(nw_scenarios) != 0:
        logger.info("nw_scenarios: %s", str(type(nw_scenarios[0])))
        logger.info("nw_scenarios: %s", str(nw_scenarios))
        # Wait for the MEC Sandbox is running
        time.sleep(STABLE_TIME_OUT) # Wait for k8s pods up and running
    else:
        logger.info("nw_scenarios: No scenario available")

    # Activate a network scenario based on a list of criterias (hard coded!!!)
    if activate_network_scenario(sandbox) == -1:
        logger.error("Failed to activate network scenario")
    else:
        logger.info("Network scenario activated: " + nw_scenarios[nw_scenario_idx].id)
        # Wait for the MEC services are running
        time.sleep(STABLE_TIME_OUT) # Wait for k8s pods up and running

    # Check that the network scenario is activated and the MEC services are running 
    logger.info("To check that the network scenario is activated, verify on the MEC Sandbox server that the MEC services are running (kubectl get pods -A")
    time.sleep(60) # Sleep for 3 seconds

    # Deactivate a network scenario based on a list of criterias (hard coded!!!)
    if deactivate_network_scenario(sandbox) == -1:
        logger.error("Failed to deactivate network scenario")
    else:
        logger.info("Network scenario deactivated: " + nw_scenarios[nw_scenario_idx].id)
        # Wait for the MEC services are terminated
        time.sleep(STABLE_TIME_OUT)

    # Logout
    process_logout(sandbox)

    # Check that logout is effective
    logger.debug("To check that logout is effective, verify on the MEC Sandbox server that the MEC Sandbox is removed (kubectl get pods -A")
  
    logger.debug("Stopped at " + time.strftime("%Y%m%d-%H%M%S"))
    # End of function process_main

if __name__ == '__main__':
    process_main()


### Fourth step: Create and delete an appliction instance id

To enable our MEC application to be part of the activated network scenario, we need to request the MEC sandbox to create a new application instance identifer. Our MEC application will use this identifier to register to the MEC Sandbox according to MEC 011.

#### The appliction instance id creation function



In [15]:
def request_application_instance_id(sandbox: str) -> swagger_client.models.ApplicationInfo:
    """
    """

    global MEC_SANDBOX_API_URL, MEC_PLTF, logger, configuration

    logger.debug(">>> request_application_instance_id: " + sandbox)

    # Create a instance of our MEC application
    a = swagger_client.models.ApplicationInfo(id=str(uuid.uuid4()), name='JupyterMecApp', node_name=MEC_PLTF, type='USER')  # noqa: E501
    print(a)
    
    try:
        nw = swagger_client.SandboxAppInstancesApi(api)
        result = nw.sandbox_app_instances_post(a, sandbox, async_req = False)  # noqa: E501
        logger.debug("request_application_instance_id: result: " + str(result))
        return result
    except ApiException as e:
        logger.error("Exception when calling SandboxAppInstancesApi->sandbox_app_instances_post: %s\n" % e)

    return None
    # End of function request_application_instance_id

#### The appliction instance id deletion function



In [14]:
def delete_application_instance_id(sandbox: str, id: str) -> int:
    """
    """

    global MEC_SANDBOX_API_URL, logger, configuration

    logger.debug(">>> deletet_application_instance_id: " + sandbox)
    logger.debug(">>> deletet_application_instance_id: " + id)

    try:
        nw = swagger_client.SandboxAppInstancesApi(api)
        result = nw.sandbox_app_instances_delete(sandbox, id, async_req = False)  # noqa: E501
        logger.debug("deletet_application_instance_id: result: " + str(result))
        return result
    except ApiException as e:
        logger.error("Exception when calling SandboxAppInstancesApi->sandbox_app_instances_delete: %s\n" % e)

    return -1
    # End of function deletet_application_instance_id

It is time now to create the our third iteration of our MEC application.

The sequence is the following:
- Login
- Print sandbox identifier
- Print available network scenarios
- Activate a network scenario
- Request for a new application instance identifer
- Check 
- Delete our application instance identifer
- Deactivate a network scenario
- Logout
- Check that logout is effective


In [16]:
def process_main():
    """
    This is the second sprint of our skeleton of our MEC application:
        - Login
        - Print sandbox identifier
        - Print available network scenarios
        - Activate a network scenario
        - Check that the network scenario is activated and the MEC services are running
        - Deactivate a network scenario
        - Logout
        - Check that logout is effective
    """ 
    global PROVIDER, MEC_SANDBOX_API_URL, logger, nw_scenarios

    logger.debug("Starting at " + time.strftime("%Y%m%d-%H%M%S"))
    logger.debug("\t pwd= " + os.getcwd())

    # Login
    sandbox = process_login()
    if sandbox is None:
        logger.error("Failed to instanciate a MEC Sandbox")
        return

    # Print sandbox identifier
    logger.info("Sandbox created: " + sandbox)
    # Wait for the MEC Sandbox is running
    time.sleep(STABLE_TIME_OUT) # Wait for k8s pods up and running

    # Print available network scenarios
    nw_scenarios = get_network_scenarios(sandbox)
    if nw_scenarios is None:
        logger.error("Failed to retrieve the list of network scenarios")
    elif len(nw_scenarios) != 0:
        logger.info("nw_scenarios: %s", str(type(nw_scenarios[0])))
        logger.info("nw_scenarios: %s", str(nw_scenarios))
        # Wait for the MEC Sandbox is running
        time.sleep(STABLE_TIME_OUT) # Wait for k8s pods up and running
    else:
        logger.info("nw_scenarios: No scenario available")

    # Activate a network scenario based on a list of criterias (hard coded!!!)
    if activate_network_scenario(sandbox) == -1:
        logger.error("Failed to activate network scenario")
    else:
        logger.info("Network scenario activated: " + nw_scenarios[nw_scenario_idx].id)
        # Wait for the MEC services are running
        time.sleep(STABLE_TIME_OUT) # Wait for k8s pods up and running

    # Request for a new application instance identifer
    app_inst_id = request_application_instance_id(sandbox)
    if app_inst_id == None:
        logger.error("Failed to request an application instance identifer")
    else:
        logger.info("app_inst_id: %s", str(type(app_inst_id)))
        logger.info("app_inst_id: %s", str(app_inst_id))

    # Check that the network scenario is activated and the MEC services are running 
    logger.info("To check that the app_inst_id is created, verify on the MEC Sandbox server that the MEC services are running (kubectl get pods -A")
    time.sleep(3) # Sleep for 3 seconds

    # Delete the application instance identifer
    if delete_application_instance_id(sandbox, app_inst_id.id) == -1:
        logger.error("Failed to delete the application instance identifer")
    else:
        logger.info("app_inst_id deleted: " + app_inst_id.id)

    # Deactivate a network scenario based on a list of criterias (hard coded!!!)
    if deactivate_network_scenario(sandbox) == -1:
        logger.error("Failed to deactivate network scenario")
    else:
        logger.info("Network scenario deactivated: " + nw_scenarios[nw_scenario_idx].id)
        # Wait for the MEC services are terminated
        time.sleep(STABLE_TIME_OUT)

    # Logout
    process_logout(sandbox)

    # Check that logout is effective
    logger.debug("To check that logout is effective, verify on the MEC Sandbox server that the MEC Sandbox is removed (kubectl get pods -A")
  
    logger.debug("Stopped at " + time.strftime("%Y%m%d-%H%M%S"))
    # End of function process_main

if __name__ == '__main__':
    process_main()


2024-06-19 08:33:18,020 - __main__ - DEBUG - Starting at 20240619-083318
2024-06-19 08:33:18,021 - __main__ - DEBUG - 	 pwd= /home/yann/dev/jupyter/Sandbox/mecapp
2024-06-19 08:33:18,023 - __main__ - DEBUG - >>> process_login
2024-06-19 08:33:18,024 DEBUG Resetting dropped connection: mec-platform.etsi.org
/usr/lib/python3/dist-packages/urllib3/connectionpool.py:1020: InsecureRequestWarning: Unverified HTTPS request is being made to host 'mec-platform.etsi.org'. Adding certificate verification is strongly advised. See: https://urllib3.readthedocs.io/en/latest/advanced-usage.html#ssl-warnings
  warnings.warn(
2024-06-19 08:33:18,285 DEBUG https://mec-platform.etsi.org:443 "POST /sandbox-api/v1/login?provider=Jupyter2024 HTTP/1.1" 201 48
2024-06-19 08:33:18,287 DEBUG response body: b'{"user_code":"sbx0rphiwx","verification_uri":""}'
2024-06-19 08:33:18,291 - __main__ - DEBUG - process_login (step1): oauth: {'user_code': 'sbx0rphiwx', 'verification_uri': ''}
2024-06-19 08:33:18,293 - __ma

send: b'POST /sandbox-api/v1/login?provider=Jupyter2024 HTTP/1.1\r\nHost: mec-platform.etsi.org\r\nAccept-Encoding: identity\r\nContent-Length: 2\r\nAccept: application/json\r\nContent-Type: application/json\r\nUser-Agent: Swagger-Codegen/1.0.0/python\r\n\r\n'
send: b'{}'
reply: 'HTTP/1.1 201 Created\r\n'
header: Date: Wed, 19 Jun 2024 06:33:17 GMT
header: Content-Type: application/json; charset=UTF-8
header: Content-Length: 48
header: Connection: keep-alive
header: Strict-Transport-Security: max-age=15724800; includeSubDomains


/usr/lib/python3/dist-packages/urllib3/connectionpool.py:1020: InsecureRequestWarning: Unverified HTTPS request is being made to host 'mec-platform.etsi.org'. Adding certificate verification is strongly advised. See: https://urllib3.readthedocs.io/en/latest/advanced-usage.html#ssl-warnings
  warnings.warn(
2024-06-19 08:33:21,333 DEBUG https://mec-platform.etsi.org:443 "GET /sandbox-api/v1/namespace?user_code=sbx0rphiwx HTTP/1.1" 200 29
2024-06-19 08:33:21,335 DEBUG response body: b'{"sandbox_name":"sbx0rphiwx"}'
2024-06-19 08:33:21,338 - __main__ - DEBUG - process_login (step2): result: {'sandbox_name': 'sbx0rphiwx'}
2024-06-19 08:33:21,339 - __main__ - INFO - Sandbox created: sbx0rphiwx


send: b'GET /sandbox-api/v1/namespace?user_code=sbx0rphiwx HTTP/1.1\r\nHost: mec-platform.etsi.org\r\nAccept-Encoding: identity\r\nAccept: application/json\r\nContent-Type: application/json\r\nUser-Agent: Swagger-Codegen/1.0.0/python\r\n\r\n'
reply: 'HTTP/1.1 200 OK\r\n'
header: Date: Wed, 19 Jun 2024 06:33:20 GMT
header: Content-Type: application/json; charset=UTF-8
header: Content-Length: 29
header: Connection: keep-alive
header: Strict-Transport-Security: max-age=15724800; includeSubDomains


2024-06-19 08:33:27,346 - __main__ - DEBUG - >>> get_network_scenarios: sandbox=sbx0rphiwx
2024-06-19 08:33:27,349 DEBUG Resetting dropped connection: mec-platform.etsi.org
/usr/lib/python3/dist-packages/urllib3/connectionpool.py:1020: InsecureRequestWarning: Unverified HTTPS request is being made to host 'mec-platform.etsi.org'. Adding certificate verification is strongly advised. See: https://urllib3.readthedocs.io/en/latest/advanced-usage.html#ssl-warnings
  warnings.warn(
2024-06-19 08:33:27,526 DEBUG https://mec-platform.etsi.org:443 "GET /sandbox-api/v1/sandboxNetworkScenarios?sandbox_name=sbx0rphiwx HTTP/1.1" 200 157
2024-06-19 08:33:27,528 DEBUG response body: b'[{"id":"4g-5g-macro-v2x"},{"id":"4g-5g-wifi-macro"},{"id":"4g-macro"},{"id":"4g-wifi-macro"},{"id":"dual-mep-4g-5g-wifi-macro"},{"id":"dual-mep-short-path"}]'
2024-06-19 08:33:27,531 - __main__ - DEBUG - get_network_scenarios: result: [{'id': '4g-5g-macro-v2x'}, {'id': '4g-5g-wifi-macro'}, {'id': '4g-macro'}, {'id': '4g

...

send: b'DELETE /sandbox-api/v1/sandboxAppInstances/sbx0rphiwx/102da481-2524-4e40-b9b0-8dfc5c7a20f9 HTTP/1.1\r\nHost: mec-platform.etsi.org\r\nAccept-Encoding: identity\r\nContent-Length: 2\r\nContent-Type: application/json\r\nUser-Agent: Swagger-Codegen/1.0.0/python\r\n\r\n'
send: b'{}'
reply: ''
send: b'DELETE /sandbox-api/v1/sandboxAppInstances/sbx0rphiwx/102da481-2524-4e40-b9b0-8dfc5c7a20f9 HTTP/1.1\r\nHost: mec-platform.etsi.org\r\nAccept-Encoding: identity\r\nContent-Length: 2\r\nContent-Type: application/json\r\nUser-Agent: Swagger-Codegen/1.0.0/python\r\n\r\n'
send: b'{}'
reply: 'HTTP/1.1 204 No Content\r\n'
header: Date: Wed, 19 Jun 2024 06:33:42 GMT
header: Content-Type: application/json; charset=UTF-8
header: Connection: keep-alive
header: Strict-Transport-Security: max-age=15724800; includeSubDomains
send: b'DELETE /sandbox-api/v1/sandboxNetworkScenarios/sbx0rphiwx/4g-5g-macro-v2x HTTP/1.1\r\nHost: mec-platform.etsi.org\r\nAccept-Encoding: identity\r\nContent-Length: 2\r\nCo

2024-06-19 08:33:43,246 DEBUG https://mec-platform.etsi.org:443 "DELETE /sandbox-api/v1/sandboxNetworkScenarios/sbx0rphiwx/4g-5g-macro-v2x HTTP/1.1" 204 0
2024-06-19 08:33:43,248 DEBUG response body: b''
2024-06-19 08:33:43,250 - __main__ - DEBUG - deactivate_network_scenario: result: None
2024-06-19 08:33:43,254 - __main__ - INFO - Network scenario deactivated: 4g-5g-macro-v2x


reply: 'HTTP/1.1 204 No Content\r\n'
header: Date: Wed, 19 Jun 2024 06:33:42 GMT
header: Content-Type: application/json; charset=UTF-8
header: Connection: keep-alive
header: Strict-Transport-Security: max-age=15724800; includeSubDomains


2024-06-19 08:33:49,262 - __main__ - DEBUG - >>> process_logout: sandbox=sbx0rphiwx
2024-06-19 08:33:49,265 DEBUG Resetting dropped connection: mec-platform.etsi.org
/usr/lib/python3/dist-packages/urllib3/connectionpool.py:1020: InsecureRequestWarning: Unverified HTTPS request is being made to host 'mec-platform.etsi.org'. Adding certificate verification is strongly advised. See: https://urllib3.readthedocs.io/en/latest/advanced-usage.html#ssl-warnings
  warnings.warn(
2024-06-19 08:33:49,416 DEBUG https://mec-platform.etsi.org:443 "POST /sandbox-api/v1/logout?sandbox_name=sbx0rphiwx HTTP/1.1" 204 0
2024-06-19 08:33:49,418 DEBUG response body: b''
2024-06-19 08:33:49,420 - __main__ - DEBUG - To check that logout is effective, verify on the MEC Sandbox server that the MEC Sandbox is removed (kubectl get pods -A
2024-06-19 08:33:49,421 - __main__ - DEBUG - Stopped at 20240619-083349


send: b'POST /sandbox-api/v1/logout?sandbox_name=sbx0rphiwx HTTP/1.1\r\nHost: mec-platform.etsi.org\r\nAccept-Encoding: identity\r\nContent-Length: 2\r\nContent-Type: application/json\r\nUser-Agent: Swagger-Codegen/1.0.0/python\r\n\r\n'
send: b'{}'
reply: 'HTTP/1.1 204 No Content\r\n'
header: Date: Wed, 19 Jun 2024 06:33:48 GMT
header: Content-Type: application/json; charset=UTF-8
header: Connection: keep-alive
header: Strict-Transport-Security: max-age=15724800; includeSubDomains


## MEC Registration and the READY confirmation

Having an application instance identifier allows us to register to the MEC Sandbox and interacts with it (e.g. to send service queries, to subscribe to events and to recieve notifications...).

The standard MEC 011 Clause 5.2.2 MEC application start-up describes the start up process. Basically, our MEC application has to:
1. Indicates that it is running by sending a Confirm Ready message
2. Retrieve the list of MEC services 

To do so, a MEC application need to be able to send request but also to recieve notifications (POST requests) and to reply to them.

### Fifth step: Send the READY confirmation

Sending READY confirmation is described by MEC 011 Clause 5.2.2 MEC application start-up.




In [ ]:
def send_ready_confirmation(app_inst_id: str) -> int:
    global MEC_SANDBOX_URL, MEC_PLTF, logger

    try:
        url = MEC_SANDBOX_URL + '/' + MEC_PLTF + '/mec_app_support/v2/applications/' + app_inst_id + '/confirm_ready'
        header_params = {}
        # HTTP header `Accept`
        header_params['Accept'] = self.api_client.select_header_accept(['application/json'])  # noqa: E501
        # HTTP header `Content-Type`
        header_params['Content-Type'] = self.api_client.select_header_accept(['application/json'])  # noqa: E501
        body = '{\"indication\":\"READY\"}'
        result = api.call_api(url, 'POST', header_params=header_params, body=body, async_req=False)
        return 0
    except ApiException as e:
        logger.error("Exception when calling AuthorizationApi->logout: %s\n" % e)
    return -1
    # End of function send_ready_confirmation

In [ ]:
def send_termination() -> int:
    pass

It is time now to create the our third iteration of our MEC application.

The sequence is the following:
- Login
- Print sandbox identifier
- Print available network scenarios
- Activate a network scenario
- Request for a new application instance identifer
- Send READY confirmation
- Get MEC services
- Check list of services 
- Delete our application instance identifer
- Deactivate a network scenario
- Logout
- Check that logout is effective


In [ ]:
def process_main():
    """
    This is the second sprint of our skeleton of our MEC application:
        - Login
        - Print sandbox identifier
        - Print available network scenarios
        - Activate a network scenario
        - Request for a new application instance identifer
        - Send READY confirmation
        - Get MEC services
        - Send Termination
        - Delete our application instance identifer
        - Deactivate a network scenario
        - Logout
        - Check that logout is effective
    """ 
    global PROVIDER, MEC_SANDBOX_API_URL, logger, nw_scenarios

    logger.debug("Starting at " + time.strftime("%Y%m%d-%H%M%S"))
    logger.debug("\t pwd= " + os.getcwd())

    # Login
    sandbox = process_login()
    if sandbox is None:
        logger.error("Failed to instanciate a MEC Sandbox")
        return

    # Print sandbox identifier
    logger.info("Sandbox created: " + sandbox)
    # Wait for the MEC Sandbox is running
    time.sleep(STABLE_TIME_OUT) # Wait for k8s pods up and running

    # Print available network scenarios
    nw_scenarios = get_network_scenarios(sandbox)
    if nw_scenarios is None:
        logger.error("Failed to retrieve the list of network scenarios")
    elif len(nw_scenarios) != 0:
        logger.info("nw_scenarios: %s", str(type(nw_scenarios[0])))
        logger.info("nw_scenarios: %s", str(nw_scenarios))
        # Wait for the MEC Sandbox is running
        time.sleep(STABLE_TIME_OUT) # Wait for k8s pods up and running
    else:
        logger.info("nw_scenarios: No scenario available")

    # Activate a network scenario based on a list of criterias (hard coded!!!)
    if activate_network_scenario(sandbox) == -1:
        logger.error("Failed to activate network scenario")
    else:
        logger.info("Network scenario activated: " + nw_scenarios[nw_scenario_idx].id)
        # Wait for the MEC services are running
        time.sleep(STABLE_TIME_OUT) # Wait for k8s pods up and running

    # Request for a new application instance identifer
    app_inst_id = request_application_instance_id(sandbox)
    if app_inst_id == None:
        logger.error("Failed to request an application instance identifer")
    else:
        logger.info("app_inst_id: %s", str(type(app_inst_id)))
        logger.info("app_inst_id: %s", str(app_inst_id))

    # Send READY confirmation
    send_ready_confirmation(app_inst_id)

    # Check list of services

    # Delete the application instance identifer
    if delete_application_instance_id(sandbox) == -1:
        logger.error("Failed to delete the application instance identifer")
    else:
        logger.info("app_inst_id deleted: " + app_inst_id.id)

    # Deactivate a network scenario based on a list of criterias (hard coded!!!)
    if deactivate_network_scenario(sandbox) == -1:
        logger.error("Failed to deactivate network scenario")
    else:
        logger.info("Network scenario deactivated: " + nw_scenarios[nw_scenario_idx].id)
        # Wait for the MEC services are terminated
        time.sleep(STABLE_TIME_OUT)

    # Logout
    process_logout(sandbox)

    # Check that logout is effective
    logger.debug("To check that logout is effective, verify on the MEC Sandbox server that the MEC Sandbox is removed (kubectl get pods -A")
  
    logger.debug("Stopped at " + time.strftime("%Y%m%d-%H%M%S"))
    # End of function process_main

if __name__ == '__main__':
    process_main()


### Notification support

To recieve notifcation, our MEC application is required to support an HTTP listenener to recieve POST request from the MEC Sandbox and replto repry to them: this is the notification mechanism.

The class HTTPRequestHandler (see cell below) provides the suport of such mechanism.


In [ ]:
class HTTPRequestHandler(BaseHTTPRequestHandler):

    def do_POST(self):
        if re.search(CALLBACK_URI, self.path):
            ctype, pdict = _parse_header(self.headers.get("content-type"))
            if ctype == "application/json":
                length = int(self.headers.get("content-length"))
                rfile_str = self.rfile.read(length).decode("utf8")
                data = parse.parse_qs(rfile_str, keep_blank_values=True)
                record_id = self.path.split("/")[-1]
                LocalData.records[record_id] = data
                print("addrecord %s: %s" % (record_id, data))
                self.send_response(HTTPStatus.OK)
            else:
                self.send_response(HTTPStatus.BAD_REQUEST, 'Only application/json is supported')
        else:
            self.send_response(HTTPStatus.BAD_REQUEST, 'Unsupported URI')
        self.end_headers()

    def do_GET(self):
        self.send_response(HTTPStatus.BAD_REQUEST)
        self.end_headers()
    # End of class HTTPRequestHandler

class LocalData(object):
    records = {}
    # End of class LocalData

In [ ]:
def process():
    # Start notification server in a daemonized thread
    notification_server = threading.Thread(name='notification_server', target=start_server, args=(LISTENER_IP, LISTENER_PORT))
    notification_server.setDaemon(True) # Set as a daemon so it will be killed once the main thread is dead.
    notification_server.start()
    # Continue


# Annexes

## Annex A: How to use an existing MEC sandbox instance

TODO



# Bibliography

1. ETSI GS MEC 002 (V2.2.1) (01-2022): "Multi-access Edge Computing (MEC); Phase 2: Use Cases and Requirements".
2. ETSI GS MEC 010-1 (V1.1.1) (10-2017): "Mobile Edge Computing (MEC); Mobile Edge Management; Part 1: System, host and platform management".
3. ETSI GS MEC 010-2 (V2.2.1) (02-2022): "Multi-access Edge Computing (MEC); MEC Management; Part 2: Application lifecycle, rules and requirements management".
4. ETSI GS MEC 011 (V3.1.1) (09-2022): "Multi-access Edge Computing (MEC); Edge Platform Application Enablement".
5. ETSI GS MEC 012 (V2.2.1) (02-2022): "Multi-access Edge Computing (MEC); Radio Network Information API".
6. ETSI GS MEC 013 (V2.2.1) (01-2022): "Multi-access Edge Computing (MEC); Location API".
7. ETSI GS MEC 014 (V2.1.1) (03-2021): "Multi-access Edge Computing (MEC); UE Identity API".
8. ETSI GS MEC 015 (V2.1.1) (06-2020): "Multi-Access Edge Computing (MEC); Traffic Management APIs".
9. ETSI GS MEC 016 (V2.2.1) (04-2020): "Multi-access Edge Computing (MEC); Device application interface".
10. ETSI GS MEC 021 (V2.2.1) (02-2022): "Multi-access Edge Computing (MEC); Application Mobility Service API".
11. ETSI GS MEC 028 (V2.3.1) (07-2022): "Multi-access Edge Computing (MEC); WLAN Access Information API".
12. ETSI GS MEC 029 (V2.2.1) (01-2022): "Multi-access Edge Computing (MEC); Fixed Access Information API".
13. ETSI GS MEC 030 (V2.2.1) (05-2022): "Multi-access Edge Computing (MEC); V2X Information Service API".
14. ETSI GR MEC-DEC 025 (V2.1.1) (06-2019): "Multi-access Edge Computing (MEC); MEC Testing Framework".
15. ETSI GR MEC 001 (V3.1.1) (01-2022): "Multi-access Edge Computing (MEC); Terminology".
16. [The Wiki MEC web site](https://www.etsi.org/technologies/multi-access-edge-computing)
17. 